For the determinatino of SFE, we'll be following the work of Reed and Schramm

SFE = 

In [ ]:
import sympy as sp
K111 = sp.Symbol("K_{111}")
w0 = sp.Symbol("\omega_{0}")
G111 = sp.Symbol("G_{111}")
a0 = sp.Symbol("a_{0}")


# Sample Preparation for Cast and HIPed Stellite 1

## Material Sourcing and Initial States

*Bulk Materials*: Obtain Stellite 1 in both cast and Hot Isostatically Pressed (HIPed) forms. It is essential to have an accurate chemical composition analysis for both. These as-received cast and HIPed states will serve as your primary microstructural references for the bulk material.

*Powder Materials*: Utilize two distinct Stellite 1 powder samples:
- Initial Powder: This is the base Stellite 1 powder before any mechanical processing. It represents the starting condition.
- Ball-Milled Powder: This is the initial powder that has been subjected to high-energy ball milling.




### Notes for Vi on why the XRD on gas atomized powder is good

In order to make the samples, Deloro Stellite made gas-atomized powders that were then blended to make the blended samples, in addition to the regular HIPed samples. These gas-atomized powders undergo extremely high cooling rates that are extremely fine-grained - in short, they will have extremely high dislocation density that will greatly increase the microstrain.

What's quite cool is that the HIPed samples are essentially the same powders but raised to 1200C and then slowly cooled down. While the carbides are the likely the same size (as noticed by Heathcock in similar work), the matrix is likely to be as relaxed as possible. Any deformation due to the carbides will be the same in the gas-atomized powders anyway.

What's even cooler is that I can see the relaxed state in the XRD plots, as the peaks are quite sharp. I should really do an estimation of grain size first, haha. 

Perhaps, we could do what the guiys in did:File material away from the solid cast speciments. Anneal the filed chips under vacuum at 1210 C for 30 minutes and then quench the water to "freeze" the dislocation-free fcc-metal matrix without the precipitation of M7C3 carbides. We could ball mill these? Or perhaps, we just take the gas-atomized powder, anneal it and quench that instead. 

UPDATE! Had a quick conversation with RA, and it does seem like if they've done XRD on one powder, they've proabably done it on all of them. Even then, he still has the powders! So it's doable :D

## Determining stacking fault probability with Popa

Stacking faults cause the (200) peak in cobalt to shift its position, while the (111) peak remains fixed. Thus, by comparing the difference between (200) - (111) on a fault-free (FF) sample and a fault-dense (FD) sample, we can measure the exact probability or amount of stacking faults.

Stacking fault probability gives a measure of how many {111} planes have stacking fault, which is critical for understanding mechanical behavior like work hardening, twinning, and phase transformation.



$$
\Delta 2 \Theta = {\left( 2 {\color{blue}\Theta_{200}} - 2 {\color{blue}\Theta_{111}} \right)}_{FF} - {\left( 2 {\color{green}\Theta_{200}} - 2 {\color{green}\Theta_{111}} \right)}_{FD}  =  - {\color{red}\alpha} \frac{45\sqrt{3}}{\pi^2} {\left( tan {\color{blue}\Theta_{200}} - 0.5 tan {\color{blue}\Theta_{111}} \right)}_{FF} 
$$

the color coding is to make this easier on the eye: blue - FF, green - FD, red - alpha

In [3]:
import numpy

def calculate_stacking_fault_probability_from_angles(
    theta_111_FD,  
    theta_200_FD,  
    theta_111_FF,  
    theta_200_FF   
):
    """
    Calculates the stacking fault probability (alpha) directly from 
    (111) and (200) 2-theta peak positions (in radians) for FD (e.g., fully deformed) 
    and FF (e.g., fault-free/annealed) states.

    Args:
        theta_111_FD (float): theta angle of (111) peak in the FD state (radians).
        theta_200_FD (float): theta angle of (200) peak in the FD state (radians).
        theta_111_FF (float): theta angle of (111) peak in the FF state (radians).
        theta_200_FF (float): theta angle of (200) peak in the FF state (radians).

    Returns:
        float: The calculated stacking fault probability (alpha).

    Raises:
        TypeError: If any of the input angles are not numbers.
        ValueError: If the denominator for alpha calculation (tan terms) is too close to zero.
    """

    # Part 0: Input validation for initial angles
    for angle_name, angle_value in [
        ("theta_111_FD", theta_111_FD),
        ("theta_200_FD", theta_200_FD),
        ("theta_111_FF", theta_111_FF),
        ("theta_200_FF", theta_200_FF)
    ]:
        if not isinstance(angle_value, (int, float)):
            raise TypeError(f"{angle_name} must be a number. Got: {angle_value}")

    
    # Part 1: Calculate delta 2-theta separation (in radians)
    delta_2theta_separation = (2*theta_200_FD - 2*theta_111_FD) - (2*theta_200_FF - 2*theta_111_FF)

    # Part 2: Calculate stacking fault probability    
    denominator_tan_terms = numpy.tan(theta_200_FD) + 0.5 * numpy.tan(theta_111_FD)
    alpha = -(numpy.pi**2 / (45.0 * numpy.sqrt(3.0))) * delta_2theta_separation / denominator_tan_terms
    
    # Part 3: Warnings for alpha values
    if alpha < 0:
        print(f"Warning: Calculated stacking fault probability (alpha) is negative ({alpha:.4e}). "
              "This may indicate issues with input peak shift data (e.g., incorrect peak indexing, "
              "peak shifts in the opposite direction to that expected for faulting), "
              "or unusual faulting behavior not described by the simple Warren model. "
              "The resulting SFE may not be physically meaningful for a stable FCC material.")
    elif abs(alpha) < 1e-9:
        print(f"Warning: Calculated stacking fault probability (alpha) is very close to zero ({alpha:.4e}). "
              "This suggests negligible faulting, or that the peak shifts are too small to be "
              "reliably measured or distinguished from experimental error. "
              "SFE calculated from this alpha will be very large or approach infinity.")
              
    return alpha

In [4]:
# Example values in RADIANS (replace with actual experimental data)
# Scenario 1: Typical positive alpha
# Original degrees: 43.50, 50.50, 43.70, 50.80
# delta_2theta_separation_deg = (50.50 - 43.50) - (50.80 - 43.70) = 7.00 - 7.10 = -0.10 deg
theta_111_FD = numpy.radians(43.50)/2  # FD (111) in radians
theta_200_FD = numpy.radians(50.50)/2  # FD (200) in radians
theta_111_FF = numpy.radians(43.70)/2  # FF (111) in radians
theta_200_FF = numpy.radians(50.80)/2  # FF (200) in radians
        
alpha1 = calculate_stacking_fault_probability_from_angles(
    theta_111_FD,
    theta_200_FD,
    theta_111_FF,
    theta_200_FF    
)

print(f"Calculated SFP (alpha): {alpha1:.4e}")

Calculated SFP (alpha): 3.2931e-04
